In [ ]:
import numpy as np
import pandas as pd
import plotly.express as px
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import json
import folium


from statsmodels.tsa.seasonal import seasonal_decompose
from scipy.signal import find_peaks
from scipy.signal import argrelextrema
from plotly.subplots import make_subplots

import geopandas as gpd
from shapely.geometry import Point
from folium.plugins import MarkerCluster

In [ ]:
contacts = pd.read_excel('/content/Contacts_clear.xlsx', dtype={'Id': str})
calls = pd.read_excel('/content/Calls_clear.xlsx', dtype={'Id': str, "CONTACTID": str})
spend = pd.read_excel('/content/Spend_clear.xlsx')
deals = pd.read_excel('/content/Deals_clear.xlsx', dtype={'Id': str, 'Contact Name': str})

In [ ]:
calls.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 92617 entries, 0 to 92616
Data columns (total 12 columns):
 #   Column                      Non-Null Count  Dtype         
---  ------                      --------------  -----         
 0   Unnamed: 0                  92617 non-null  int64         
 1   Id                          92617 non-null  object        
 2   Call Start Time             92617 non-null  datetime64[ns]
 3   Call Owner Name             92617 non-null  object        
 4   CONTACTID                   88815 non-null  object        
 5   Call Type                   92617 non-null  object        
 6   Call Duration (in seconds)  92538 non-null  float64       
 7   Call Status                 92617 non-null  object        
 8   Dialled Number              0 non-null      float64       
 9   Outgoing Call Status        83804 non-null  object        
 10  Scheduled in CRM            83804 non-null  float64       
 11  Tag                         0 non-null      float64   

In [ ]:
deals.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19788 entries, 0 to 19787
Data columns (total 24 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   Unnamed: 0           19788 non-null  int64         
 1   Id                   19788 non-null  object        
 2   Deal Owner Name      19788 non-null  object        
 3   Closing Date         13129 non-null  datetime64[ns]
 4   Quality              17557 non-null  object        
 5   Stage                19788 non-null  object        
 6   Lost Reason          14347 non-null  object        
 7   Page                 19788 non-null  object        
 8   Campaign             15555 non-null  object        
 9   Content              13771 non-null  object        
 10  Term                 12077 non-null  object        
 11  Source               19788 non-null  object        
 12  Payment Type         482 non-null    object        
 13  Product              3537 non-n

In [ ]:
contacts.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18548 entries, 0 to 18547
Data columns (total 5 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   Unnamed: 0          18548 non-null  int64         
 1   Id                  18548 non-null  object        
 2   Contact Owner Name  18548 non-null  object        
 3   Created Time        18548 non-null  datetime64[ns]
 4   Modified Time       18548 non-null  datetime64[ns]
dtypes: datetime64[ns](2), int64(1), object(2)
memory usage: 724.7+ KB


In [ ]:
spend.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15057 entries, 0 to 15056
Data columns (total 9 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   Unnamed: 0   15057 non-null  int64         
 1   Date         15057 non-null  datetime64[ns]
 2   Source       15057 non-null  object        
 3   Campaign     13804 non-null  object        
 4   Impressions  15057 non-null  int64         
 5   Spend        15057 non-null  float64       
 6   Clicks       15057 non-null  int64         
 7   AdGroup      12970 non-null  object        
 8   Ad           12970 non-null  object        
dtypes: datetime64[ns](1), float64(1), int64(3), object(4)
memory usage: 1.0+ MB


===================================================================================================


# Анализ временных рядов:




====================================================================================================

1. Проанализируйте тенденцию создания сделок с течением времени и ее связь со звонками



Для выполнения поставленных задач необходимо объединить таблицы.


In [ ]:
deals_contacts = pd.merge(deals, contacts, left_on='Contact Name', right_on='Id',
                          how='left')
calls_contacts = pd.merge(calls, contacts, left_on='CONTACTID', right_on='Id',
                          how='left')
deals_spend = pd.merge(deals, spend, on='Campaign', how='outer')

In [ ]:
deals_contacts.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19788 entries, 0 to 19787
Data columns (total 29 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   Unnamed: 0_x         19788 non-null  int64         
 1   Id_x                 19788 non-null  object        
 2   Deal Owner Name      19788 non-null  object        
 3   Closing Date         13129 non-null  datetime64[ns]
 4   Quality              17557 non-null  object        
 5   Stage                19788 non-null  object        
 6   Lost Reason          14347 non-null  object        
 7   Page                 19788 non-null  object        
 8   Campaign             15555 non-null  object        
 9   Content              13771 non-null  object        
 10  Term                 12077 non-null  object        
 11  Source               19788 non-null  object        
 12  Payment Type         482 non-null    object        
 13  Product              3537 non-n

In [ ]:
calls_contacts.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 92617 entries, 0 to 92616
Data columns (total 17 columns):
 #   Column                      Non-Null Count  Dtype         
---  ------                      --------------  -----         
 0   Unnamed: 0_x                92617 non-null  int64         
 1   Id_x                        92617 non-null  object        
 2   Call Start Time             92617 non-null  datetime64[ns]
 3   Call Owner Name             92617 non-null  object        
 4   CONTACTID                   88815 non-null  object        
 5   Call Type                   92617 non-null  object        
 6   Call Duration (in seconds)  92538 non-null  float64       
 7   Call Status                 92617 non-null  object        
 8   Dialled Number              0 non-null      float64       
 9   Outgoing Call Status        83804 non-null  object        
 10  Scheduled in CRM            83804 non-null  float64       
 11  Tag                         0 non-null      float64   

Агрегирование данных по звонкам и сделкам по месяцам

In [ ]:
deals_by_time = deals_contacts.resample(
            'ME', on='Created Time_y').size().reset_index(name='Deals Count')
calls_by_time = calls_contacts.resample(
            'ME', on='Call Start Time').size().reset_index(name='Calls Count')

In [ ]:
deals_by_time.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12 entries, 0 to 11
Data columns (total 2 columns):
 #   Column          Non-Null Count  Dtype         
---  ------          --------------  -----         
 0   Created Time_y  12 non-null     datetime64[ns]
 1   Deals Count     12 non-null     int64         
dtypes: datetime64[ns](1), int64(1)
memory usage: 324.0 bytes


In [ ]:
calls_by_time.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13 entries, 0 to 12
Data columns (total 2 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   Call Start Time  13 non-null     datetime64[ns]
 1   Calls Count      13 non-null     int64         
dtypes: datetime64[ns](1), int64(1)
memory usage: 340.0 bytes


In [ ]:
time_series_data = pd.merge(deals_by_time, calls_by_time,
                            left_on='Created Time_y',
                            right_on='Call Start Time',
                            how='outer')
time_series_data = time_series_data.rename(columns={'Created Time_y': 'Date'})

In [ ]:
time_series_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13 entries, 0 to 12
Data columns (total 4 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   Date             12 non-null     datetime64[ns]
 1   Deals Count      12 non-null     float64       
 2   Call Start Time  13 non-null     datetime64[ns]
 3   Calls Count      13 non-null     int64         
dtypes: datetime64[ns](2), float64(1), int64(1)
memory usage: 548.0 bytes


# Создайте визуализацию тенденции создания сделок и звонков по времени

In [ ]:
fig = px.line(time_series_data,
              x='Date',
              y=['Deals Count', 'Calls Count'],
              title='Ежемесячная тенденция создания сделок и звонков',
              labels={'value': 'Quantity', 'variable': ''},
              template='plotly_white', markers=True)

for i, column in enumerate(['Deals Count', 'Calls Count']):
    fig.data[i].update(
        text=time_series_data[column],
        textposition="top center",
        mode="lines+markers+text"
    )

fig.update_layout(
    title_x=0.5,
    xaxis_title="",
    legend=dict(
    orientation="h",
    x=0.5,
    xanchor="center",
    y=1.1
    )
)

fig.show()

# Заключение:

Анализ графика показывает, что динамика звонков и сделок за рассматриваемый период различается. Количество звонков значительно возросло, достигнув наивысшей точки в мае 2024 года, после чего наблюдалось снижение. Количество сделок также увеличилось, однако этот рост был более постепенным, без резких пиков. Примечательно, что пиковое значение как звонков, так и сделок приходится на май 2024 года, что может свидетельствовать о взаимосвязи между активностью звонков и успешным завершением сделок. Важно отметить, что общее число сделок существенно ниже числа совершенных звонков, что подчеркивает необходимость повышения эффективности процесса конвертации звонков в результативные сделки.

In [ ]:
deals_by_time_w = deals_contacts.resample(
            'W', on='Created Time_y').size().reset_index(name='Deals Count')
calls_by_time_w = calls_contacts.resample(
            'W', on='Call Start Time').size().reset_index(name='Calls Count')

In [ ]:
time_series_data_w = pd.merge(deals_by_time_w, calls_by_time_w,
                            left_on='Created Time_y',
                            right_on='Call Start Time',
                            how='outer')
time_series_data_w = time_series_data_w.rename(columns={'Created Time_y': 'Date'})

In [ ]:
def find_extrema(series):
    indexes_max = argrelextrema(series.values, np.greater, order=2)[0]
    return indexes_max

fig = px.line(time_series_data_w,
              x='Date',
              y=['Deals Count', 'Calls Count'],
              title='Недельный срез сделок и звонков',
              labels={'value': 'Quantuty', 'variable': ''},
              template='plotly_white', markers=True)

for i, column in enumerate(['Deals Count', 'Calls Count']):
    indexes_max = find_extrema(time_series_data_w[column].fillna(0))
    text_labels = ['' if idx not in indexes_max else f'{int(val)}'
                   for idx, val in enumerate(time_series_data_w[column])]

    fig.data[i].update(
        text=text_labels,
        textposition="top center",
        mode="lines+markers+text"
    )

    x_vals = np.arange(len(time_series_data_w))
    y_vals = time_series_data_w[column].fillna(0).values
    trend = np.polyfit(x_vals, y_vals, deg=1)
    trend_line = np.polyval(trend, x_vals)

    fig.add_scatter(x=time_series_data_w['Date'], y=trend_line, mode='lines',
                    name=f'{column} Trend', line=dict(dash='dot'))

fig.update_layout(
    title_x=0.5,
    xaxis_title="",
    legend=dict(
    orientation="h",
    x=0.5,
    xanchor="center",
    y=1.1
    )
)

fig.show()

# Общий вывод по обоим графикам:
Согласно глобальному (ежемесячному) анализу, наблюдался стабильный подъём звонков и сделок вплоть до мая 2024 года, после чего произошёл резкий спад. Детальный (еженедельный) анализ показывает циклическое увеличение активности каждые 3-4 недели. Закономерно, пики звонков обычно предшествуют увеличению числа сделок. Резкое снижение показателей после мая 2024 года является поводом для дальнейшего исследования с целью определения вызвавших его факторов, таких как сезонность или изменения в маркетинговой стратегии.


# Рекомендации:

Предлагается провести анализ событий мая 2024 года для определения факторов, вызвавших всплеск активности (маркетинговые кампании, скидки, изменения стратегии). Также следует изучить 3-4-недельный цикл с целью его оптимизации, в частности, поиска способов увеличения количества звонков в периоды спада. Кроме того, необходимо исследовать причины резкого падения показателей после мая 2024 года и разработать потенциальные решения для стабилизации или восстановления роста.
--------------------------------------------------------------------------------

In [ ]:
def transfer_to_week(df, time_column, target_column=None):
    df_copy = df.copy()
    result = pd.DataFrame()

    if target_column is not None:
        weekly_time_series = (
            df_copy.set_index(time_column)
            .resample('W')[target_column]
            .sum()
            .reset_index()
        )
        result['Date'] = weekly_time_series[time_column]
        result['Target'] = weekly_time_series[target_column]

    else:
        weekly_time_series = (
            df_copy.set_index(time_column)
            .resample('W')
            .size()
            .reset_index()
        )
        result['Date'] = weekly_time_series[time_column]
        result['Target'] = weekly_time_series[0]

    return result

In [ ]:
spend_w = transfer_to_week(spend,'Date', 'Spend')
contacts_w = transfer_to_week(contacts, 'Created Time')
deals_w = transfer_to_week(deals, 'Created Time')
calls_w = transfer_to_week(calls, 'Call Start Time')

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=deals_w['Date'],
                         y=deals_w['Target'],
                         mode='lines+markers',
                         name='Deals Count (Weekly)'))
fig.add_trace(go.Scatter(x=calls_w['Date'],
                         y=calls_w['Target'],
                         mode='lines+markers',
                         name='Calls Count (Weekly)'))
fig.add_trace(go.Scatter(x=contacts_w['Date'],
                         y=contacts_w['Target'],
                         mode='lines+markers',
                         name='Contacts Count (Weekly)',
                         line=dict(dash='dash')))
fig.add_trace(go.Scatter(x=spend_w['Date'],
                         y=spend_w['Target'],
                         mode='lines+markers',
                         name='Ad Spend (Weekly)',
                         line=dict(dash='dot')))

fig.update_layout(
    title='Еженедельные тенденции сделок',
    title_x=0.5,
    yaxis_title='Траты',
    legend_title='',
    legend=dict(orientation="h", x=0.5, xanchor="center", y=1.1),
    xaxis=dict(tickangle=0),
    template='plotly_white')

fig.show()

# Выводы из графика


Рост числа сделок и звонков тесно коррелирует с увеличением маркетинговых затрат, причем иногда рост расходов предшествует увеличению активности клиентов, что подтверждает ключевую роль маркетинга в привлечении. Количество новых контактов демонстрирует более умеренный и стабильный рост, возможно, указывая на насыщение наиболее заинтересованной аудитории и снижение эффективности привлечения новых. Наблюдается цикличность: пики рекламных расходов сменяются всплесками звонков и сделок с интервалом в несколько недель, что свидетельствует об эффективности маркетинговой стратегии, но требует оценки рентабельности инвестиций. После майского пика 2024 года заметен резкий спад всех показателей, включая звонки, сделки и рекламные расходы, что требует выяснения причин, будь то смена стратегии, сезонность или перераспределение бюджета.

In [ ]:
time_series_data_cleaned_w = time_series_data_w.dropna(subset=['Deals Count'])
decomposition_deals = seasonal_decompose(
    time_series_data_cleaned_w['Deals Count'],model='multiplicative', period=12)

trend_deals = decomposition_deals.trend
seasonal_deals = decomposition_deals.seasonal
residual_deals = decomposition_deals.resid

decomposition_calls = seasonal_decompose(time_series_data_cleaned_w['Calls Count'], model='multiplicative', period=12)
trend_calls = decomposition_calls.trend
seasonal_calls = decomposition_calls.seasonal
residual_calls = decomposition_calls.resid

In [ ]:
def plot_series_subplot(fig, series, title, color, row, col):
    if series is not None:
        fig.add_trace(go.Scatter(
                x=time_series_data_cleaned_w.index,
                y=series, mode="lines", name=title, line=dict(color=color)), row=row, col=col,)

fig = make_subplots(rows=3, cols=2, subplot_titles=("Trend - Deals Count", "Trend - Calls Count", "Seasonality - Deals Count", "Seasonality - Calls Count", "Residuals - Deals Count", "Residuals - Calls Count"
))
plot_series_subplot(fig, trend_deals, "Trend - Deals Count", "orange", 1, 1)
plot_series_subplot(fig, trend_calls, "Trend - Calls Count", "green", 1, 2)

plot_series_subplot(fig, seasonal_deals, "Seasonality - Deals Count", "orange", 2, 1)
plot_series_subplot(fig, seasonal_calls, "Seasonality - Calls Count", "green", 2, 2)

plot_series_subplot(fig, residual_deals, "Residuals - Deals Count", "orange", 3, 1)
plot_series_subplot(fig, residual_calls, "Residuals - Calls Count", "green", 3, 2)

fig.update_layout(height=900, width=1200, showlegend=False)
fig.show()
fig_initial = make_subplots(rows=1, cols=2, subplot_titles=("Initial Data - Deals Count", "Initial Data - Calls Count"))

plot_series_subplot(
    fig_initial, time_series_data_cleaned_w["Deals Count"], "Initial Data - Deals Count", "orange", 1, 1)
if "Calls Count" in time_series_data_cleaned_w.columns: plot_series_subplot(fig_initial, time_series_data_cleaned_w["Calls Count"], "Initial Data - Calls Count", "green", 1, 2)

fig_initial.update_layout(height=400, width=1200, showlegend=False)
fig_initial.show()

# Выводы:

Общая тенденция:

Наблюдается общий рост как количества звонков, что может свидетельствовать об увеличении интереса клиентов или активизации маркетинга, так и числа сделок, хотя последний растёт более умеренно и стабильно.

Сезонность:

В динамике звонков и сделок чётко прослеживается двухнедельная сезонность, вероятно связанная с регулярными маркетинговыми мероприятиями или акциями, влияющими на поведение потребителей. Учитывая эти циклические колебания, рекомендуется синхронизировать маркетинговые кампании с выявленными периодами активности для оптимального охвата целевой аудитории.

Остальные:

Анализ остатков выявляет случайные колебания, не объясняемые общей тенденцией или сезонностью. Нерегулярные события, влияющие на количество звонков и сделок, отражаются в остаточных временных рядах. Изучение причин этих спорадических отклонений может способствовать повышению стабильности ключевых показателей.

---------------------------------------------------------------------------------------------

# 2. Анализ времени и продолжительности закрытия сделки от создания до закрытия

----------------------------------------------------------------------------------------------

Анализ выбросов в датах закрытия сделок (выбросы дат закрытия):


In [ ]:
max_date = deals_contacts['Closing Date'].max()
print(min_date, max_date)

2022-10-11 00:00:00 2024-12-11 00:00:00


In [ ]:
min_date1 = deals['Created Time'].min()
max_date1 = deals['Created Time'].max()
print(min_date1, max_date1)

2023-07-03 17:03:00 2024-06-21 15:30:00


In [ ]:
deals_contacts = deals_contacts[deals_contacts['Closing Date'] >= min_date1]

In [ ]:
fig = px.box(deals_contacts, x='Closing Date', title='Closing Date')

fig.update_layout(
    xaxis_title="Closing Date Outliers",
    yaxis_title="",
    showlegend=False,
    template="plotly_white"
)

fig.show()

Анализ распределения длительностей сделок (Duration):

In [ ]:
deals_contacts['Duration'] = abs((deals_contacts['Closing Date'] - deals_contacts['Created Time_x']).dt.days)

<ipython-input-41-318e49683b22>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
deals_contacts.columns

Index(['Unnamed: 0_x', 'Id_x', 'Deal Owner Name', 'Closing Date', 'Quality',
       'Stage', 'Lost Reason', 'Page', 'Campaign', 'Content', 'Term', 'Source',
       'Payment Type', 'Product', 'Education Type', 'Created Time_x',
       'Course duration', 'Months of study', 'Initial Amount Paid',
       'Offer Total Amount', 'Contact Name', 'City', 'Level of Deutsch',
       'SLA Seconds', 'Unnamed: 0_y', 'Id_y', 'Contact Owner Name',
       'Created Time_y', 'Modified Time', 'Duration'],
      dtype='object')

In [ ]:
deals_contacts['Duration'].value_counts()

Duration
1      3467
0      1594
2       938
3       778
4       622
       ... 
205       1
304       1
231       1
300       1
246       1
Name: count, Length: 234, dtype: int64

In [ ]:
fig = px.histogram(deals_contacts, x='Duration', title='Продолжительность', nbins=30)

fig.update_layout(
    xaxis_title="Duration",
    yaxis_title="Count",
    showlegend=False,
    template="plotly_white")
fig.show()

In [ ]:
Q1 = deals_contacts['Duration'].quantile(0.25)
Q3 = deals_contacts['Duration'].quantile(0.75)
IQR = Q3 - Q1

lower_whisker = Q1 - 1.5 * IQR
upper_whisker = Q3 + 1.5 * IQR

outliers = deals_contacts[(deals_contacts['Duration'] < lower_whisker) |
                          (deals_contacts['Duration'] > upper_whisker)]
num_outliers = len(outliers)

total_points = len(deals_contacts)

outlier_percentage = (num_outliers / total_points) * 100

print(f"Number of outliers: {num_outliers} out of {total_points} records")
print(f"Percentage of outliers: {outlier_percentage:.2f}%")

Number of outliers: 1930 out of 13127 records
Percentage of outliers: 14.70%


Визуализация распределения дат закрытия сделок:

In [ ]:
deals_contacts_filtered = deals_contacts[
    (deals_contacts['Duration'] >= lower_whisker) &
    (deals_contacts['Duration'] <= upper_whisker)]

fig = make_subplots(
    rows=1,
    cols=2,
    subplot_titles=[
        "Распределение дат закрытия сделок", "Распределение продолжительности сделки",],)

fig.add_trace(
    go.Histogram(
        x=deals_contacts_filtered["Closing Date"],
        nbinsx=30,
        marker_color="orange",
        name="Closing Date",
    ), row=1, col=1,)

fig.add_trace(
    go.Histogram(
        x=deals_contacts_filtered["Duration"],
        nbinsx=30,
        marker_color="green",
        name="Duration", ), row=1, col=2,)

closing_date_min = deals_contacts_filtered["Closing Date"].min()
closing_date_max = deals_contacts_filtered["Closing Date"].max()
duration_min = deals_contacts_filtered["Duration"].min()
duration_max = deals_contacts_filtered["Duration"].max()

fig.update_xaxes(
    range=[closing_date_min - pd.Timedelta(days=10),
           closing_date_max + pd.Timedelta(days=10)], row=1,  col=1,)
fig.update_xaxes(range=[duration_min - 1, duration_max + 1], row=1, col=2)

fig.update_layout(
    height=500,
    bargap=0.1,
    showlegend=False,)

fig.update_xaxes(title_text="Closing Date", row=1, col=1)
fig.update_yaxes(title_text="Number of Deals", row=1, col=1)

fig.update_xaxes(title_text="Duration (days)", row=1, col=2)
fig.update_yaxes(title_text="Number of Deals", row=1, col=2)

fig.show()

Заключение:
Закрытие сделок в 2024 году пиково в феврале и апреле, в остальное время более равномерно, что указывает на возможную сезонность или влияние факторов. Большинство сделок закрываются быстро (до 10 дней), что говорит об эффективности продаж, но редкие длительные закрытия (до 140 дней) требуют изучения для улучшения процессов.

====================================================================================================

# 2. Анализ эффективности кампании:

====================================================================================================

1.Сравните эффективность различных кампаний с точки зрения генерации лидов и коэффициентов конверсии.


2.Оцените эффективность различных маркетинговых источников (Источник) в привлечении высококачественных лидов.

In [ ]:
deals_spend.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14885177 entries, 0 to 14885176
Data columns (total 32 columns):
 #   Column               Dtype         
---  ------               -----         
 0   Unnamed: 0_x         float64       
 1   Id                   object        
 2   Deal Owner Name      object        
 3   Closing Date         datetime64[ns]
 4   Quality              object        
 5   Stage                object        
 6   Lost Reason          object        
 7   Page                 object        
 8   Campaign             object        
 9   Content              object        
 10  Term                 object        
 11  Source_x             object        
 12  Payment Type         object        
 13  Product              object        
 14  Education Type       object        
 15  Created Time         datetime64[ns]
 16  Course duration      float64       
 17  Months of study      float64       
 18  Initial Amount Paid  float64       
 19  Offer Total Amount 

In [ ]:
deals_spend.describe()

Unnamed: 0_x                   Closing Date  \
count  1.488469e+07                       10106562   
mean   1.148598e+04  2024-01-23 18:13:30.859008256   
min    0.000000e+00            2022-10-11 00:00:00   
25%    7.128000e+03            2023-11-13 00:00:00   
50%    1.189200e+04            2024-01-30 00:00:00   
75%    1.619600e+04            2024-04-08 00:00:00   
max    2.159200e+04            2024-12-11 00:00:00   
std    5.802649e+03                            NaN   

                        Created Time  Course duration  Months of study  \
count                       14884691     2.985139e+06    713890.000000   
mean   2024-01-18 15:45:25.361359872     1.023178e+01         5.424825   
min              2023-07-03 17:03:00     6.000000e+00         0.000000   
25%              2023-11-18 13:26:00     1.100000e+01         3.000000   
50%              2024-01-23 07:10:00     1.100000e+01         5.000000   
75%              2024-03-27 13:41:00     1.100000e+01         8.000000   
max              2024-06-21 15:30:00     1.100000e+01        11.000000   
std                              NaN     1.803035e+00         2.880723   

       Initial Amount Paid  Offer Total Amount   SLA Seconds  Unnamed: 0_y  \
count         1.488469e+07        1.488469e+07  1.184410e+07  1.487935e+07   
mean          2.089123e+02        1.667205e+03  1.090908e+05  9.980629e+03   
min           0.000000e+00        0.000000e+00  3.000000e+00  0.000000e+00   
25%           0.000000e+00        0.000000e+00  4.238000e+03  5.070000e+03   
50%           0.000000e+00        0.000000e+00  1.953000e+04  9.820000e+03   
75%           0.000000e+00        0.000000e+00  5.518400e+04  1.471100e+04   
max           1.100000e+04        1.150000e+04  2.690846e+07  2.077800e+04   
std           7.011497e+02        3.758794e+03  7.176778e+05  5.824899e+03   

                                Date   Impressions         Spend        Clicks  
count                       14879349  1.487935e+07  1.487935e+07  1.487935e+07  
mean   2024-01-08 07:56:12.696507392  2.223545e+03  1.235124e+01  3.518887e+01  
min              2023-07-03 00:00:00  0.000000e+00  0.000000e+00  0.000000e+00  
25%              2023-10-10 00:00:00  3.000000e+01  0.000000e+00  1.000000e+00  
50%              2024-01-18 00:00:00  3.680000e+02  1.490000e+00  8.000000e+00  
75%              2024-04-07 00:00:00  1.461000e+03  7.630000e+00  3.200000e+01  
max              2024-06-21 00:00:00  4.314450e+05  7.740000e+02  2.415000e+03  
std                              NaN  7.582586e+03  4.996030e+01  7.571029e+01

In [ ]:
deals_spend.head()

Unnamed: 0_x   Id Deal Owner Name Closing Date Quality Stage Lost Reason  \
0           NaN  NaN             NaN          NaT     NaN   NaN         NaN   
1           NaN  NaN             NaN          NaT     NaN   NaN         NaN   
2           NaN  NaN             NaN          NaT     NaN   NaN         NaN   
3           NaN  NaN             NaN          NaT     NaN   NaN         NaN   
4           NaN  NaN             NaN          NaT     NaN   NaN         NaN   

  Page                 Campaign Content  ... Level of Deutsch SLA Seconds  \
0  NaN  01.02.24wide_webinar_DE     NaN  ...              NaN         NaN   
1  NaN  01.02.24wide_webinar_DE     NaN  ...              NaN         NaN   
2  NaN  01.02.24wide_webinar_DE     NaN  ...              NaN         NaN   
3  NaN  01.02.24wide_webinar_DE     NaN  ...              NaN         NaN   
4  NaN  01.02.24wide_webinar_DE     NaN  ...              NaN         NaN   

  Unnamed: 0_y       Date Source_y Impressions  Spend  Clicks  AdGroup  \
0      10778.0 2024-02-03  Webinar      2927.0  33.14    24.0     wide   
1      10780.0 2024-02-03  Webinar       771.0   6.40     4.0     wide   
2      10816.0 2024-02-04  Webinar      3076.0  33.78    33.0     wide   
3      10838.0 2024-02-04  Webinar       182.0   1.52     2.0     wide   
4      10870.0 2024-02-05  Webinar       801.0   7.72    10.0     wide   

          Ad  
0  v1webinar  
1  v2webinar  
2  v1webinar  
3  v2webinar  
4  v2webinar  

[5 rows x 32 columns]

In [ ]:
spend[['Campaign', 'Source']] = spend[['Campaign', 'Source']].astype('category')

In [ ]:
source_leads = deals_spend[deals_spend['Source_y'] != 'Test'].groupby('Source_y', observed=True).size().reset_index(name='Leads')
source_leads

Source_y    Leads
0         Bloggers  1096347
1              CRM   334407
2     Facebook Ads  4592389
3       Google Ads   165558
4          Offline    33864
5          Organic   977823
6      Partnership    63495
7            Radio     8466
8              SMM   745008
9   Telegram posts  1985277
10      Tiktok Ads  2844723
11         Webinar    73259
12     Youtube Ads  1951832

In [ ]:
spend[spend['Source'] == 'Test']

Unnamed: 0       Date Source         Campaign  Impressions  Spend  \
5629         7410 2023-12-01   Test              NaN            0   0.00   
5799         7679 2023-12-08   Test  07.12.23test_DE           93   1.37   
5803         7683 2023-12-08   Test  07.12.23test_DE            2   0.00   
5810         7692 2023-12-08   Test  07.12.23test_DE           17   0.22   
5812         7694 2023-12-08   Test  07.12.23test_DE           13   0.26   
...           ...        ...    ...              ...          ...    ...   
13086       17790 2024-05-11   Test  02.05.24test_DE            1   0.02   
13094       17807 2024-05-11   Test  02.05.24test_DE         1888  15.59   
13113       17829 2024-05-12   Test  02.05.24test_DE         2698  18.36   
13116       17835 2024-05-12   Test  02.05.24test_DE            1   0.02   
13182       17938 2024-05-13   Test  02.05.24test_DE         1413   9.25   

       Clicks                AdGroup                  Ad  
5629        0                    NaN                 NaN  
5799        0       wide_webdesigner       b3webdesigner  
5803        0  wide_python-developer  b1python-developer  
5810        0       wide_qa-engineer       b1qa-engineer  
5812        0  wide_python-developer  b3python-developer  
...       ...                    ...                 ...  
13086       0        accountant_wide        b2accountant  
13094      76        accountant_wide        b3accountant  
13113      83        accountant_wide        b3accountant  
13116       0        accountant_wide        b1accountant  
13182      46        accountant_wide        b3accountant  

[170 rows x 9 columns]

In [ ]:
spend[spend['Source'] == 'Test'].describe()

Unnamed: 0                           Date  Impressions       Spend  \
count    170.000000                            170   170.000000  170.000000   
mean    9208.352941  2024-01-01 05:04:56.470588160   258.641176    3.577706   
min     7410.000000            2023-12-01 00:00:00     0.000000    0.000000   
25%     7873.750000            2023-12-11 00:00:00    13.250000    0.302500   
50%     8107.000000            2023-12-15 12:00:00    56.500000    1.290000   
75%     8317.500000            2023-12-19 00:00:00   273.250000    5.800000   
max    17938.000000            2024-05-13 00:00:00  2698.000000   18.920000   
std     3117.713074                            NaN   493.492343    4.645094   

           Clicks  
count  170.000000  
mean     7.211765  
min      0.000000  
25%      0.000000  
50%      1.000000  
75%      6.000000  
max    110.000000  
std     18.901861

In [ ]:
spend['Source'].value_counts()

Source
Facebook Ads      8749
Tiktok Ads        2242
Youtube Ads       1424
Google Ads         912
Telegram posts     469
Webinar            321
Bloggers           259
Organic            231
SMM                176
Test               170
CRM                 79
Partnership         15
Offline              8
Radio                2
Name: count, dtype: int64

In [ ]:
source_leads = deals.groupby('Source', as_index=False)['Id'].count()
source_leads.columns = ['Source', 'Leads']

# Группируем по источнику только успешные сделки (Stage == 'Won')
successful_deals = deals[deals['Stage'] == 'Won'].groupby('Source', as_index=False)['Id'].count()
successful_deals.columns = ['Source', 'Successful Deals']

# Объединяем две таблицы
source_performance = pd.merge(source_leads, successful_deals, on='Source', how='outer')

# Заполняем пропуски и рассчитываем конверсию
source_performance['Successful Deals'] = source_performance['Successful Deals'].fillna(0)
source_performance['Conversion Rate (%)'] = (source_performance['Successful Deals'] / source_performance['Leads']) * 100
source_performance



Source  Leads  Successful Deals  Conversion Rate (%)
0         Bloggers   1071               0.0                  0.0
1              CRM   1455               0.0                  0.0
2     Facebook Ads   4711               0.0                  0.0
3       Google Ads   4110               0.0                  0.0
4          Offline      2               0.0                  0.0
5          Organic   1497               0.0                  0.0
6      Partnership    201               0.0                  0.0
7              SMM   1668               0.0                  0.0
8   Telegram posts    993               0.0                  0.0
9             Test    156               0.0                  0.0
10      Tiktok Ads   2001               0.0                  0.0
11         Webinar    305               0.0                  0.0
12     Youtube Ads   1618               0.0                  0.0

In [ ]:
print("CONTACTS COLUMNS:", contacts.columns.tolist())
print("DEALS COLUMNS:", deals.columns.tolist())

CONTACTS COLUMNS: ['Unnamed: 0', 'Id', 'Contact Owner Name', 'Created Time', 'Modified Time']
DEALS COLUMNS: ['Unnamed: 0', 'Id', 'Deal Owner Name', 'Closing Date', 'Quality', 'Stage', 'Lost Reason', 'Page', 'Campaign', 'Content', 'Term', 'Source', 'Payment Type', 'Product', 'Education Type', 'Created Time', 'Course duration', 'Months of study', 'Initial Amount Paid', 'Offer Total Amount', 'Contact Name', 'City', 'Level of Deutsch', 'SLA Seconds']


In [ ]:
source_performance = pd.merge(source_leads, successful_deals, on='Source',
                              how='outer')
source_performance['Successful Deals'] = source_performance['Successful Deals'].fillna(0)
source_performance['Conversion Rate'] = source_performance['Successful Deals'] /source_performance['Leads'] * 100
source_performance

Source  Leads  Successful Deals  Conversion Rate
0         Bloggers   1071               0.0              0.0
1              CRM   1455               0.0              0.0
2     Facebook Ads   4711               0.0              0.0
3       Google Ads   4110               0.0              0.0
4          Offline      2               0.0              0.0
5          Organic   1497               0.0              0.0
6      Partnership    201               0.0              0.0
7              SMM   1668               0.0              0.0
8   Telegram posts    993               0.0              0.0
9             Test    156               0.0              0.0
10      Tiktok Ads   2001               0.0              0.0
11         Webinar    305               0.0              0.0
12     Youtube Ads   1618               0.0              0.0

In [ ]:
fig = go.Figure(go.Bar(
    x=source_performance['Source'],
    y=source_performance['Leads'],
    name='Leads',
    marker_color='green',
    text=source_performance['Leads'],
    textposition='outside'
))

fig.update_layout(
    title=dict(
        text="Количество лидов",
        x=0.5,
        xanchor="center",
        font=dict(size=18)),
    xaxis=dict(title="Source", tickangle=-45),
    yaxis=dict(title="Number of Leads", showgrid=False),
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1,
        xanchor="center",
        x=0.5),
    height=600,
    width=1000,
    template="plotly_white")

fig.show()

# Выводы из графика:

Лидеры по лидам: Facebook (4.57M), TikTok (2.79M), YouTube (1.95M).  Рекомендация: фокус на Facebook, TikTok и YouTube.


========================================================================================================


# 3. Анализ эффективности работы отдела продаж:




=========================================================================================================




-- Подсчет количества обработанных сделок, успешных сделок и общей суммы платежей --

In [ ]:
owner_deals = deals.groupby(
    'Deal Owner Name',
    observed=True)['Id'].nunique().reset_index(name='Total Deals')

successful_owner_deals = (
    deals[deals['Stage'] == 'Payment Done']
    .groupby('Deal Owner Name', observed=True)['Id']
    .nunique()
    .reset_index(name='Successful Deals')
)

total_sales = deals[
    deals['Stage'] == 'Payment Done'].groupby(
        'Deal Owner Name', observed=True)['Offer Total Amount'].sum().reset_index()

In [ ]:
owner_performance = pd.merge(
    owner_deals, successful_owner_deals, on='Deal Owner Name', how='left')
owner_performance = pd.merge(
    owner_performance, total_sales, on='Deal Owner Name', how='left')

owner_performance.fillna(
    {'Successful Deals': 0, 'Offer Total Amount': 0}, inplace=True)

owner_performance['Conversion Rate'] = owner_performance[
                  'Successful Deals'] / owner_performance['Total Deals'] * 100

owner_performance_sorted = owner_performance.sort_values(
                    by='Successful Deals', ascending=False)

display(owner_performance_sorted.style.format({
    'Successful Deals': '{:,.0f}',
    'Offer Total Amount': '{:,.0f}',
    'Conversion Rate': '{:.2f}'
}).hide(axis='index'))

In [ ]:
owner_performance_sorted_conversion = owner_performance.sort_values(
                    by='Conversion Rate', ascending=False)

owner_performance_sorted_conversion.head()

Deal Owner Name  Total Deals  Successful Deals  Offer Total Amount  \
16   Oliver Taylor          160              50.0            524500.0   
11        John Doe           12               1.0                 0.0   
13    Kevin Parker          500              40.0            211900.0   
21   Ulysses Adams         2069             141.0           1011400.0   
5    Charlie Davis         2797             148.0           1066600.0   

    Conversion Rate  
16        31.250000  
11         8.333333  
13         8.000000  
21         6.814886  
5          5.291384

In [ ]:
Q1_T = owner_performance['Total Deals'].quantile(0.25)

owner_performance_f_deals = owner_performance[
    owner_performance['Total Deals'] > Q1_T
]

Q1_S = owner_performance_f_deals[
    owner_performance_f_deals['Successful Deals'] > 0
]['Successful Deals'].quantile(0.25)

owner_performance_f_deals = owner_performance_f_deals[
    owner_performance_f_deals['Successful Deals'] > Q1_S
]

owner_performance_f_deals_conversion = owner_performance_f_deals.sort_values(
    by='Conversion Rate', ascending=False
)

display(owner_performance_f_deals_conversion.style.format({
    'Total Deals': '{:,.0f}',
    'Successful Deals': '{:,.0f}',
    'Offer Total Amount': '{:,.0f}',
    'Conversion Rate': '{:.2f}'
}).hide(axis='index'))

# Выводы, основанные на таблице эффективности работы менеджеров

Кара Айверсон демонстрирует самый низкий коэффициент конверсии среди менеджеров (2,52%), закрыв всего 26 сделок из 1033 попыток. Джейн Смит также показывает низкую эффективность, закрыв 31 сделку из 904 (3,43%).

Оливер Тейлор лидирует по эффективности с самым высоким коэффициентом конверсии (31,25%), успешно закрыв 50 из 160 сделок. Это может свидетельствовать о высоком качестве его лидов или сильных навыках продаж.

Чарли Дэвис обрабатывает наибольшее количество сделок (2797), но его коэффициент конверсии относительно низок (5,29%), что привело к 148 успешным сделкам. Это может указывать на работу с менее целевыми лидами или необходимость улучшения стратегии закрытия.

# ***Рекомендации***

Изучить методы продаж Оливера Тейлора (высокая конверсия) для возможного внедрения у других менеджеров. Улучшить эффективность Чарли Дэвиса и Улисса Адамса (большой объем, средняя конверсия). Пересмотреть подход к работе Кары Айверсон и Джейн Смит (низкая конверсия), возможно, проблема в лидах или требуется обучение.


In [ ]:
oliver_deals = deals[deals['Deal Owner Name'] == 'Oliver Taylor']
oliver_quality_distribution = oliver_deals[
                      'Quality'].value_counts(normalize=True) * 100

oliver_contacts = contacts[contacts['Contact Owner Name'] == 'Oliver Taylor']
total_contacts = oliver_contacts.shape[0]

oliver_calls = calls[calls['Call Owner Name'] == 'Oliver Taylor']
total_calls = oliver_calls.shape[0]
call_status_distribution = oliver_calls[
                      'Call Status'].value_counts(normalize=True) * 100

oliver_campaigns = oliver_deals['Campaign'].value_counts(normalize=True) * 100

print(
    f"oliver_quality_distribution - {oliver_quality_distribution},\n"
    "====================\n"
    f"total_contacts - {total_contacts},\n"
    "====================\n"
    f"total_calls - {total_calls},\n"
    "====================\n"
    f"call_status_distribution - {call_status_distribution},\n"
    "====================\n"
    f"oliver_campaigns - {oliver_campaigns}"
)


oliver_quality_distribution - Quality
B - Medium           44.936709
C - Low              36.075949
A - High             12.658228
D - Non Target        5.696203
E - Non Qualified     0.632911
Name: proportion, dtype: float64,
total_contacts - 19,
total_calls - 10,
call_status_distribution - Call Status
Attended Dialled      90.0
Unattended Dialled    10.0
Name: proportion, dtype: float64,
oliver_campaigns - Campaign
Dis_DE                               13.675214
performancemax_digitalmarkt_ru_DE    11.965812
youtube_shorts_DE                     9.401709
02.07.23wide_DE                       9.401709
03.07.23women                         8.547009
24.09.23retargeting_DE                5.982906
12.07.2023wide_DE                     5.128205
12.09.23interests_Uxui_DE             4.273504
07.07.23LAL_DE                        4.273504
mu_DE                                 3.418803
15.07.23b_DE                          2.564103
Trigger_DE                            1.709402
05.07.23interes

# Итоговый вывод:
Оливер работает с лучшими клиентами (высокий % A и B), получает меньше, но качественные контакты (19), почти все его звонки результативны (90% ответов), лиды из эффективных кампаний. Вероятно, он фокусируется на качестве, а не количестве, работая с квалифицированными клиентами и проводя эффективные звонки. Предлагается сравнить количество назначенных контактов из тех же кампаний другим сотрудникам. Далее следует анализ эффективности отдела продаж по рекламным кампаниям (количество сделок, конверсия, общая выручка).

In [ ]:
campaign_deals = deals[deals['Campaign'] != 'Unknown'].groupby(
    'Campaign', observed=True)['Id'].nunique().reset_index(name='Total Deals')


successful_campaign_deals = deals[(deals['Stage'] == 'Payment Done') &
                            (deals['Campaign'] != 'Unknown')]\
                            .groupby('Campaign', observed=True)['Id']\
                            .nunique().reset_index(name='Successful Deals')

total_sales_campaign = deals[(deals['Stage'] == 'Payment Done') &
                             (deals['Campaign'] != 'Unknown')]\
                    .groupby('Campaign', observed=True)['Offer Total Amount']\
                    .sum().reset_index()

campaign_performance = pd.merge(campaign_deals,
                                successful_campaign_deals,
                                on='Campaign',
                                how='left')
campaign_performance = pd.merge(campaign_performance,
                                total_sales_campaign,
                                on='Campaign',
                                how='left')


campaign_performance['Successful Deals'] = campaign_performance[
    'Successful Deals'].fillna(0)
campaign_performance['Offer Total Amount'] = campaign_performance[
    'Offer Total Amount'].fillna(0)
campaign_performance['Conversion Rate'] = campaign_performance[
    'Successful Deals'] / campaign_performance['Total Deals'] * 100

campaign_performance_sorted = campaign_performance.sort_values(
    by='Successful Deals', ascending=False)

campaign_performance_sorted.columns = [
                                'Campaign', 'Total Deals', 'Successful Deals',
                                'Offer Total Amount', 'Conversion Rate']

formatted_campaign_performance_sorted = campaign_performance_sorted[
    ['Campaign', 'Total Deals', 'Successful Deals',
     'Offer Total Amount', 'Conversion Rate']].style.format({
    'Successful Deals': '{:,.0f}',
    'Offer Total Amount': '{:,.0f}',
    'Conversion Rate': '{:.2f}'
}).hide(axis='index')

display(formatted_campaign_performance_sorted)

In [ ]:
campaign_performance

Campaign  Total Deals  Successful Deals  Offer Total Amount  \
0        01.04.23women_PL           31               0.0                 0.0   
1         02.05.24test_DE          120               1.0             11000.0   
2         02.07.23wide_DE          940              52.0            396900.0   
3    02.08.23interests_DE            8               0.0                 0.0   
4           03.07.23women          592              31.0            256000.0   
..                    ...          ...               ...                 ...   
148               work_wr            6               0.0                 0.0   
149          workingin_DE           48               0.0                 0.0   
150                 yo_DE           13               0.0                 0.0   
151     youtube_shorts_DE         1596              53.0            415500.0   
152   youtube_shortsin_AT           14               0.0                 0.0   

     Conversion Rate  
0           0.000000  
1           0.833333  
2           5.531915  
3           0.000000  
4           5.236486  
..               ...  
148         0.000000  
149         0.000000  
150         0.000000  
151         3.320802  
152         0.000000  

[153 rows x 5 columns]

In [ ]:
top_10_campaigns = campaign_performance_sorted.head(10)
top_10_campaigns_cleaned = top_10_campaigns.copy()
top_10_campaigns_cleaned['Campaign'] = top_10_campaigns_cleaned['Campaign'].str[:10]

fig = go.Figure()

fig.add_trace(go.Bar(
    x=top_10_campaigns_cleaned['Campaign'],
    y=top_10_campaigns_cleaned['Total Deals'],
    name='Total Deals',
    marker_color='yellow'))

fig.add_trace(go.Bar(
    x=top_10_campaigns_cleaned['Campaign'],
    y=top_10_campaigns_cleaned['Successful Deals'],
    name='Successful Deals',
    marker_color='lightgreen'))

scaled_conversion_rate = [rate * 40 for rate in top_10_campaigns_cleaned['Conversion Rate']]

fig.add_trace(go.Scatter(
    x=top_10_campaigns_cleaned['Campaign'],
    y=scaled_conversion_rate,
    mode='lines+markers+text',
    name='Conversion Rate (%) (scaled)',
    text=[f'{rate:.1f}%' for rate in top_10_campaigns_cleaned['Conversion Rate']],
    textposition='top center'
))

fig.update_layout(
    title=dict(
        text='Топ-10 кампаний: общее количество сделок, успешные сделки и коэффициент конверсии',
        x=0.5, xanchor='center'
    ),
    xaxis_title='',
    yaxis_title='Total Deals and Successful Deals',
    yaxis2=dict(title='Conversion Rate (%)', overlaying='y', side='right'),
    legend=dict(x=0.5, y=1.07, xanchor='center', orientation='h'),
    barmode='group',
    xaxis_tickangle=0,
    height=800,
    width=1200
)

fig.show()

Выводы:

Лидер по числу сделок: performancemax_digitalmarkt_ru_DE (но конверсия 4.4%). Лучшая конверсия: 02.07.23wide_DE (5.5%, сделок меньше). Высокий объем часто = низкая конверсия, нужна оптимизация таргетинга/качества лидов.

-------------------------------------------------------------------------------------------------------

In [ ]:
print(deals_contacts.columns)

Index(['Unnamed: 0_x', 'Id_x', 'Deal Owner Name', 'Closing Date', 'Quality',
       'Stage', 'Lost Reason', 'Page', 'Campaign', 'Content', 'Term', 'Source',
       'Payment Type', 'Product', 'Education Type', 'Created Time_x',
       'Course duration', 'Months of study', 'Initial Amount Paid',
       'Offer Total Amount', 'Contact Name', 'City', 'Level of Deutsch',
       'SLA Seconds', 'Unnamed: 0_y', 'Id_y', 'Contact Owner Name',
       'Created Time_y', 'Modified Time', 'Duration'],
      dtype='object')


In [ ]:
deals_contacts['Created Time'] = pd.to_datetime(deals_contacts['Created Time_x'])
deals_contacts['Closing Date'] = pd.to_datetime(deals_contacts['Closing Date'])

deals_contacts['Duration'] = (deals_contacts['Closing Date'] - deals_contacts['Created Time']).dt.days

# Теперь продолжите фильтрацию и агрегирование
deals_contacts_noTest = deals_contacts[deals_contacts['Source'] != 'Test']
campaign_source_analysis = deals_contacts_noTest.groupby(
    ['Campaign', 'Source']
).agg(
    Mean_Time_to_Close=('Duration', 'mean'),
    Median_Time_to_Close=('Duration', 'median'),
    Total_Deals=('Stage', 'count'),
    Successful_Deals=('Stage', lambda x: (x == 'Payment Done').sum()),
    Conversion_Rate=('Stage', lambda x: (
        (x == 'Payment Done').sum() / len(x) * 100 if len(x) > 0 else 0
    ))
).reset_index()

print(campaign_source_analysis)

                     Campaign          Source  Mean_Time_to_Close  \
0            01.04.23women_PL    Facebook Ads           11.583333   
1             02.07.23wide_DE    Facebook Ads           18.451289   
2        02.08.23interests_DE    Facebook Ads           13.000000   
3               03.07.23women    Facebook Ads           20.183258   
4    04.07.23recentlymoved_DE    Facebook Ads           16.121597   
..                        ...             ...                 ...   
167              workingin_DE  Telegram posts           18.743590   
168                     yo_DE             SMM           13.100000   
169         youtube_shorts_DE      Google Ads           61.000000   
170         youtube_shorts_DE     Youtube Ads           12.778428   
171       youtube_shortsin_AT     Youtube Ads           12.000000   

     Median_Time_to_Close  Total_Deals  Successful_Deals  Conversion_Rate  
0                     5.5           24                 0         0.000000  
1                  

<ipython-input-82-3790b942e1e8>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-82-3790b942e1e8>:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-82-3790b942e1e8>:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
deals_contacts_noTest = deals_contacts[deals_contacts['Source'] != 'Test']
campaign_source_analysis = deals_contacts_noTest.groupby(
    ['Campaign', 'Source']
).agg(
    Mean_Time_to_Close=('Duration', 'mean'),
    Median_Time_to_Close=('Duration', 'median'),
    Total_Deals=('Stage', 'count'),
    Successful_Deals=('Stage', lambda x: (x == 'Payment Done').sum()),
    Conversion_Rate=('Stage', lambda x: (
        (x == 'Payment Done').sum() / len(x) * 100 if len(x) > 0 else 0
    ))
).reset_index()

campaign_detailed_analysis = deals.groupby(
    'Campaign'
).agg(
    Total_Deals=('Stage', 'count'),
    Converted_Deals=('Stage', lambda x: (x == 'Payment Done').sum()),
    Conversion_Rate=('Stage', lambda x: (
        (x == 'Payment Done').sum() / len(x) * 100 if len(x) > 0 else 0
    )),
    Total_Sales=('Initial Amount Paid', 'sum'),
    Avg_Deal_Amount=('Initial Amount Paid', lambda x: x[x > 0].mean()),
    Avg_Time_to_Close=('Closing Date', lambda x: (
        (x - deals.loc[x.index, 'Created Time']).dt.days.mean()
    ))
).reset_index()

stage_distribution_campaign = deals.pivot_table(
    index='Campaign',
    columns='Stage',
    values='Id',
    aggfunc='count',
    fill_value=0
).reset_index()

In [ ]:
campaign_source_analysis.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 172 entries, 0 to 171
Data columns (total 7 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   Campaign              172 non-null    object 
 1   Source                172 non-null    object 
 2   Mean_Time_to_Close    172 non-null    float64
 3   Median_Time_to_Close  172 non-null    float64
 4   Total_Deals           172 non-null    int64  
 5   Successful_Deals      172 non-null    int64  
 6   Conversion_Rate       172 non-null    float64
dtypes: float64(3), int64(2), object(2)
memory usage: 9.5+ KB


In [ ]:
campaign_source_analysis = deals_contacts_noTest.groupby(['Campaign', 'Source']).agg(
    Mean_Time_to_Close=('Duration', 'mean'),
    Median_Time_to_Close=('Duration', 'median'),
    Total_Deals=('Stage', 'count')).reset_index()
campaign_source_analysis = campaign_source_analysis.merge(
    campaign_performance[['Campaign', 'Successful Deals', 'Conversion Rate']],
    on='Campaign',
    how='left'
)
campaign_source_analysis

Campaign          Source  Mean_Time_to_Close  \
0            01.04.23women_PL    Facebook Ads           11.583333   
1             02.07.23wide_DE    Facebook Ads           18.451289   
2        02.08.23interests_DE    Facebook Ads           13.000000   
3               03.07.23women    Facebook Ads           20.183258   
4    04.07.23recentlymoved_DE    Facebook Ads           16.121597   
..                        ...             ...                 ...   
167              workingin_DE  Telegram posts           18.743590   
168                     yo_DE             SMM           13.100000   
169         youtube_shorts_DE      Google Ads           61.000000   
170         youtube_shorts_DE     Youtube Ads           12.778428   
171       youtube_shortsin_AT     Youtube Ads           12.000000   

     Median_Time_to_Close  Total_Deals  Successful Deals  Conversion Rate  
0                     5.5           24               0.0         0.000000  
1                     5.0          698              52.0         5.531915  
2                     4.5            8               0.0         0.000000  
3                     4.0          442              31.0         5.236486  
4                     4.0          551              31.0         4.258242  
..                    ...          ...               ...              ...  
167                   2.0           39               0.0         0.000000  
168                   4.5           10               0.0         0.000000  
169                  61.0            1              53.0         3.320802  
170                   2.0         1196              53.0         3.320802  
171                   3.5            8               0.0         0.000000  

[172 rows x 7 columns]

=======================================================================================================


# 4. Анализ платежей и продуктов:


=======================================================================================================



*   Изучите распределение типов платежей и их влияние на успешность сделок.





In [ ]:
fig.add_trace(
    go.Scatter(
        x=payment_performance['Payment Type'],
        y=payment_performance['Conversion Rate'],
        mode='lines+markers+text',
        name='Conversion Rate',
        marker=dict(color='red', size=8),
        text=payment_performance['Conversion Rate'].astype(str) + '%',
        textposition='top left')

In [ ]:
filtered_deals = deals[deals['Payment Type'].astype(str) != 'Unknown']

total_payments = (
    filtered_deals.groupby('Payment Type', observed=True)['Id']
    .nunique()
    .reset_index(name='Total Deals'))

successful_payments = (
    filtered_deals[filtered_deals['Stage'] == 'Payment Done']
    .groupby('Payment Type', observed=True)['Id']
    .nunique()
    .reset_index(name='Successful Deals'))

payment_performance = pd.merge(
    total_payments, successful_payments, on='Payment Type', how='left')

payment_performance['Successful Deals'] = (
    payment_performance['Successful Deals'].fillna(0))

payment_performance['Conversion Rate'] = (
    payment_performance['Successful Deals']
    / payment_performance['Total Deals'] * 100).round(1)

fig = px.bar(
    payment_performance,
    x='Payment Type',
    y=['Total Deals', 'Successful Deals'],
    barmode='group',
    color_discrete_map={
        'Total Deals': 'skyblue',
        'Successful Deals': 'lightgreen'},
    title='Эффективность платежей: общее количество сделок, успешные сделки, '
          'and Conversion Rate', text_auto='.2s')

for trace in fig.data:
    if 'bar' in trace.type:
        trace.textposition = 'outside'

fig.update_layout(
    title_x=0.5,
    yaxis=dict(title='Number of Deals'),
    yaxis2=dict(
        title='Conversion Rate (%)',
        overlaying='y',
        side='right',
        showgrid=False),
    xaxis_title='',
    legend_title='',
    legend=dict(
        orientation="h",
        x=0.5,
        xanchor="center",
        y=1.1),
    template='plotly_white',)

fig.show()

# Выводы из графика:

Лидер по числу сделок: "Повторяющиеся платежи" (340), затем "Один платеж" (140), минимум - "Бронирование" (5). Успешные сделки аналогично распределены. Лучшая конверсия: "Один платеж" (82.4%), ниже у "Повторяющихся платежей" (73%), самая низкая у "Бронирования" (20%). Несмотря на большее число сделок, "Повторяющиеся платежи" имеют конверсию ниже, чем "Один платеж". Рекомендация: изучить причины низкой конверсии "Повторяющихся платежей" и "Бронирования".


-------------------------------------------------------------------------------------------------------------------


# Проанализируйте популярность и показатели успешности различных продуктов и типов обучения.


-------------------------------------------------------------------------------------------------------------------

In [ ]:
filtered_deals = deals[deals['Education Type'].isin(['Morning', 'Evening'])]

education_deals = (
    filtered_deals.groupby('Education Type', observed=True)['Id']
    .nunique()
    .reset_index(name='Total Deals')
)

successful_education_deals = (
    filtered_deals[filtered_deals['Stage'] == 'Payment Done']
    .groupby('Education Type', observed=True)['Id']
    .nunique()
    .reset_index(name='Successful Deals')
)

total_sales_education = (
    filtered_deals[filtered_deals['Stage'] == 'Payment Done']
    .groupby('Education Type', observed=True)['Offer Total Amount']
    .sum()
    .reset_index()
)

education_performance = pd.merge(
    education_deals, successful_education_deals, on='Education Type', how='left'
)
education_performance = pd.merge(
    education_performance, total_sales_education, on='Education Type', how='left'
)

education_performance[['Successful Deals',
                       'Offer Total Amount']] = education_performance[
    ['Successful Deals', 'Offer Total Amount']
].fillna({'Successful Deals': 0, 'Offer Total Amount': 0})

education_performance['Conversion Rate'] = (
    education_performance['Successful Deals'] / \
    education_performance['Total Deals'] * 100
)

education_performance_sorted = education_performance.sort_values(
    by='Successful Deals', ascending=False
)

education_performance_sorted.columns = [
    'Education Type', 'Total Deals', 'Successful Deals',
    'Offer Total Amount', 'Conversion Rate'
]

formatted_education_performance_sorted = education_performance_sorted[
    ['Education Type', 'Total Deals', 'Successful Deals',
     'Offer Total Amount', 'Conversion Rate']
].style.format({
    'Successful Deals': '{:,.0f}',
    'Offer Total Amount': '{:,.0f}',
    'Conversion Rate': '{:.2f}'
}).hide(axis='index')

display(formatted_education_performance_sorted)

Вывод:

На основании данных в таблице мы видим, что утренний тип обучения привлек больше всего сделок (2984) и сгенерировал наибольшее количество продаж (5 713 800), но его коэффициент конверсии составил 22,39%. С другой стороны, вечерний тип обучения показал меньшую общую активность с 406 сделками и объемом продаж 626,30, но он все равно продемонстрировал значительно более высокий коэффициент конверсии 41,87%. Это говорит о том, что вечерние занятия, хотя и менее популярны, более эффективны в конвертации лидов в успешные сделки.

Таблица, показывающую расчет метрик по продуктам, учитывая типы обучения.


In [ ]:
product_education_deals = (
    deals.groupby(['Product', 'Education Type'], observed=True)['Id']
    .nunique()
    .reset_index(name='Total Deals')
)

successful_product_education_deals = (
    deals[deals['Stage'] == 'Payment Done']
    .groupby(['Product', 'Education Type'], observed=True)['Id']
    .nunique()
    .reset_index(name='Successful Deals')
)

total_sales_product_education = (
    deals[deals['Stage'] == 'Payment Done']
    .groupby(['Product', 'Education Type'], observed=True)['Offer Total Amount']
    .sum()
    .reset_index()
)

product_education_performance = pd.merge(
    product_education_deals, successful_product_education_deals,
    on=['Product', 'Education Type'], how='left'
)
product_education_performance = pd.merge(
    product_education_performance, total_sales_product_education,
    on=['Product', 'Education Type'], how='left'
)

product_education_performance.fillna(0, inplace=True)

product_education_performance['Conversion Rate'] = (
    product_education_performance['Successful Deals'] /
    product_education_performance['Total Deals'] * 100)

product_education_performance_sorted = product_education_performance.sort_values(
    by='Successful Deals', ascending=False
)

formatted_product_education_performance_sorted = (
    product_education_performance_sorted[
        ['Product', 'Education Type', 'Total Deals',
         'Successful Deals', 'Offer Total Amount', 'Conversion Rate']
    ]
    .style.format({
        'Total Deals': '{:,.0f}',
        'Successful Deals': '{:,.0f}',
        'Offer Total Amount': '{:,.0f}',
        'Conversion Rate': '{:.2f}'
    })
    .hide(axis='index')
)

display(formatted_product_education_performance_sorted)

Заключение:

Утренние курсы лидируют по сделкам во всех категориях, особенно "Цифровой маркетинг" (1618 сделок, 361 успешных, €3.52M, 22.31% конверсия). Вечерний "Цифровой маркетинг" также эффективен (44.66% конверсия, 253 сделки, 113 успешных). Утром популярны "UX/UI-дизайн" (815 сделок, 170 успешных) и "Веб-разработчик" (542 сделки, 137 успешных). Вечерний "UX/UI-дизайн" демонстрирует высокую конверсию (37.50%, 152 сделки, 57 успешных).

In [ ]:
pie_data = product_education_performance_sorted.groupby(
    ["Product", "Education Type"]
)["Offer Total Amount"].sum().reset_index()

In [ ]:
another_discrete_sequence = px.colors.qualitative.Pastel1

fig_treemap = px.treemap(pie_data,
                         path=['Product', 'Education Type'],
                         values='Offer Total Amount',
                         color="Education Type",
                         color_discrete_sequence=another_discrete_sequence,
                         title='Revenue Share by Product and Education Type (Treemap)',
                         template="plotly_white")
fig_treemap.show()

# Ключевые выводы из графиков:

Лидер по сделкам - утренний "Цифровой маркетинг", затем утренний "UX/UI-дизайн", меньше всего сделок у вечернего "Веб-разработчика". Утренний формат доминирует.

Основной доход - от утреннего "Цифрового маркетинга" (55.6%) и утреннего "UX/UI-дизайна" (25.4%). Вечерние программы (особенно "Веб-разработчик") приносят минимум дохода. Вклад утреннего "Веб-разработчика" и вечернего "Цифрового маркетинга" невелик.

=====================================================================================================


# 5. Географический анализ:


=====================================================================================================


1. Проанализируйте географическое распределение сделок по городам.

In [ ]:
# deals_df.to_csv("deals_u.csv", index=False)
# calls_df.to_csv("calls_u.csv", index=False)
# spend_df.to_csv("spend_u.csv", index=False)
# contacts_df.to_csv("contacts_u.csv", index=False)

In [ ]:
deals['City'] = deals.City.replace('-', "Unnamed")

In [ ]:
deals

Unnamed: 0                   Id Deal Owner Name Closing Date  \
0               0  5805028000056864695        Ben Hall          NaT   
1               1  5805028000056859489   Ulysses Adams          NaT   
2               2  5805028000056832357   Ulysses Adams   2024-06-21   
3               3  5805028000056824246        Eva Kent   2024-06-21   
4               4  5805028000056873292        Ben Hall   2024-06-21   
...           ...                  ...             ...          ...   
19783       21587  5805028000000935025    Kevin Parker   2023-07-06   
19784       21589  5805028000000948010      Jane Smith   2023-08-29   
19785       21590  5805028000000945016      Jane Smith   2023-08-29   
19786       21591  5805028000000927004       Bob Brown   2023-07-09   
19787       21592  5805028000000922001       Bob Brown   2023-07-03   

                 Quality     Stage             Lost Reason  \
0                    NaN  New Lead                     NaN   
1                    NaN  New Lead                     NaN   
2         D - Non Target      Lost              Non target   
3      E - Non Qualified      Lost          Invalid number   
4         D - Non Target      Lost              Non target   
...                  ...       ...                     ...   
19783  E - Non Qualified      Lost          Doesn't Answer   
19784         B - Medium      Lost     needs time to think   
19785           A - High      Lost        Changed Decision   
19786     D - Non Target      Lost  Does not speak English   
19787  E - Non Qualified      Lost                 Refugee   

                        Page                  Campaign             Content  \
0                  /eng/test             03.07.23women                 v16   
1                    /at-eng                       NaN                 NaN   
2                    /at-eng                engwien_AT               b1-at   
3                       /eng  04.07.23recentlymoved_DE  bloggersvideo14com   
4                       /eng              discovery_DE             website   
...                      ...                       ...                 ...   
19783  eng/digital-marketing           02.07.23wide_DE                  b3   
19784  eng/digital-marketing             03.07.23women                  b3   
19785  eng/digital-marketing           02.07.23wide_DE                  b3   
19786  eng/digital-marketing             03.07.23women                  b3   
19787                      /                       NaN                 NaN   

       ... Education Type        Created Time Course duration Months of study  \
0      ...            NaN 2024-06-21 15:30:00             NaN             NaN   
1      ...        Morning 2024-06-21 15:23:00             6.0             NaN   
2      ...            NaN 2024-06-21 14:45:00             NaN             NaN   
3      ...            NaN 2024-06-21 13:32:00             NaN             NaN   
4      ...            NaN 2024-06-21 13:21:00             NaN             NaN   
...    ...            ...                 ...             ...             ...   
19783  ...            NaN 2023-07-04 09:34:00             NaN             NaN   
19784  ...            NaN 2023-07-04 07:10:00             NaN             NaN   
19785  ...            NaN 2023-07-03 20:39:00             NaN             NaN   
19786  ...            NaN 2023-07-03 20:17:00             NaN             NaN   
19787  ...            NaN 2023-07-03 17:03:00             NaN             NaN   

      Initial Amount Paid Offer Total Amount         Contact Name  City  \
0                       0                  0  5805028000056849495   NaN   
1                       0               2000  5805028000056834471   NaN   
2                       0                  0  5805028000056854421   NaN   
3                       0                  0  5805028000056889351   NaN   
4                       0                  0  5805028000056876176   NaN   
...                   ...                ...     

In [ ]:
geo_deals_df = deals[['Id', 'City']]
geo_deals_df_clean = geo_deals_df.dropna(subset=['City'])
deals_by_city = geo_deals_df_clean.groupby('City').size().reset_index(name='Number of Deals')

deals_by_city_sorted = deals_by_city.sort_values(by='Number of Deals', ascending=False)
deals_by_city_sorted

City  Number of Deals
774    Unnamed              423
88      Berlin              264
521    München               88
288    Hamburg               78
570   Nürnberg               53
..         ...              ...
10    Aichwald                1
11   Aidlingen                1
12       Ajman                1
13    Alamudun                1
14    Albstadt                1

[871 rows x 2 columns]

In [ ]:
print(deals.columns)

Index(['Unnamed: 0', 'Id', 'Deal Owner Name', 'Closing Date', 'Quality',
       'Stage', 'Lost Reason', 'Page', 'Campaign', 'Content', 'Term', 'Source',
       'Payment Type', 'Product', 'Education Type', 'Created Time',
       'Course duration', 'Months of study', 'Initial Amount Paid',
       'Offer Total Amount', 'Contact Name', 'City', 'Level of Deutsch',
       'SLA Seconds'],
      dtype='object')


In [ ]:
with open("city_data_google.json", "r") as json_file:
    city_data = json.load(json_file)

In [ ]:
def get_city_info(city):
    info = city_data.get(city, {})
    return pd.Series({
        'longitude': info.get('longitude', None),
        'latitude': info.get('latitude', None),
        'country_ru': info.get('country', None),
        'city_ru': info.get('formatted_address', None)
    })

deals['City'] = deals['City'].fillna('Unknown')
deals[['longitude', 'latitude', 'country_ru', 'city_ru']] = deals['City'].apply(get_city_info)

In [ ]:
deals.loc[deals.City != "Unknown"].head()

Unnamed: 0                   Id  Deal Owner Name Closing Date  Quality  \
32          35  5805028000056714532    Ulysses Adams          NaT      NaN   
39          42  5805028000056731279    Ulysses Adams          NaT      NaN   
49          56  5805028000056683030    Charlie Davis          NaT  C - Low   
50          57  5805028000056568397  Paula Underwood          NaT      NaN   
53          60  5805028000056558351    Ulysses Adams          NaT  C - Low   

                    Stage Lost Reason       Page               Campaign  \
32  Registered on Webinar         NaN   /webinar            webinar1906   
39  Registered on Webinar         NaN   /webinar                    NaN   
49    Waiting For Payment         NaN  /eng/test  performancemax_eng_DE   
50  Registered on Webinar         NaN   /webinar                    NaN   
53    Waiting For Payment         NaN       /eng                    NaN   

            Content  ... Initial Amount Paid Offer Total Amount  \
32              NaN  ...                   0                  0   
39              NaN  ...                   0                  0   
49  _{region_name}_  ...                1000               9000   
50              NaN  ...                   0                  0   
53              NaN  ...                1000               9000   

           Contact Name        City Level of Deutsch SLA Seconds  longitude  \
32  5805028000044019127      Berlin       Неизвестно         NaN  13.404954   
39  5805028000054755989   Lahnstein       Неизвестно         NaN   7.609363   
49  5805028000056690015  Crailsheim       Неизвестно      1239.0  10.063357   
50  5805028000020664131    Prenzlau               B1         NaN  13.862376   
53  5805028000056578244    Dortmund               B1       589.0   7.465298   

     latitude  country_ru      city_ru  
32  52.520007    Германия       Берлин  
39  50.307827    Германия     Ланштайн  
49  49.133735    Германия  Крайльсхайм  
50  53.316844    Германия     Пренцлау  
53  51.513587    Германия     Дортмунд  

[5 rows x 28 columns]

In [ ]:
deals['City'] = deals.City.replace('-', "Unknown")

In [ ]:
deals.to_csv("deals_geo.csv", index=False)

In [ ]:
deals_dashbord = deals[deals['Stage'] == 'Payment Done'].groupby('City').agg({'Stage': 'count'}) / deals.groupby('City').agg({'Stage': 'count'}) * 100
deals_dashbord[deals_dashbord.index == 'Frankfurt']

Stage
City                
Frankfurt  20.588235

# Расчет статистики

In [ ]:
geo_deals = deals[['Id', 'City']]
geo_deals_clean = geo_deals.dropna(subset=['City'])
deals_by_city = geo_deals_clean.groupby('City').size().reset_index(name='Number of Deals')

deals_by_city_sorted = deals_by_city.sort_values(by='Number of Deals', ascending=False)
deals_by_city_sorted

City  Number of Deals
774       Unknown            16673
775       Unnamed              423
88         Berlin              264
521       München               88
288       Hamburg               78
..            ...              ...
864    Zoetermeer                1
863     Zinnowitz                1
862         Zetel                1
861        Zerbst                1
860  Zella-Mehlis                1

[872 rows x 2 columns]

In [ ]:
geo_data_deals = deals[["City", "longitude", "latitude", "country_ru",
                           "city_ru"]].drop_duplicates(subset=["City"]).dropna()

In [ ]:
deals_by_city_sorted = deals_by_city_sorted.merge(geo_data_deals, on='City', how="inner")
deals_by_city_sorted

City  Number of Deals  longitude   latitude  country_ru  \
0          Berlin              264  13.404954  52.520007    Германия   
1         München               88  11.581981  48.135125    Германия   
2         Hamburg               78   9.987170  53.548828    Германия   
3        Nürnberg               53  11.074564  49.454288    Германия   
4         Leipzig               52  12.373075  51.339695    Германия   
..            ...              ...        ...        ...         ...   
864    Zoetermeer                1   4.494025  52.060669  Нидерланды   
865     Zinnowitz                1  13.908474  54.075441    Германия   
866         Zetel                1   7.973801  53.418060    Германия   
867        Zerbst                1  12.084621  51.966948    Германия   
868  Zella-Mehlis                1  10.664964  50.658799    Германия   

         city_ru  
0         Берлин  
1         Мюнхен  
2        Гамбург  
3       Нюрнберг  
4        Лейпциг  
..           ...  
864     Зутермер  
865     Цинновиц  
866       Цетель  
867       Цербст  
868  Целла-Мелис  

[869 rows x 6 columns]

In [ ]:
deals_by_city_sorted = deals_by_city_sorted.merge(geo_data_deals, on='City', how="inner")
deals_by_city_sorted

City  Number of Deals  longitude_x  latitude_x country_ru_x  \
0          Berlin              264    13.404954   52.520007     Германия   
1         München               88    11.581981   48.135125     Германия   
2         Hamburg               78     9.987170   53.548828     Германия   
3        Nürnberg               53    11.074564   49.454288     Германия   
4         Leipzig               52    12.373075   51.339695     Германия   
..            ...              ...          ...         ...          ...   
864    Zoetermeer                1     4.494025   52.060669   Нидерланды   
865     Zinnowitz                1    13.908474   54.075441     Германия   
866         Zetel                1     7.973801   53.418060     Германия   
867        Zerbst                1    12.084621   51.966948     Германия   
868  Zella-Mehlis                1    10.664964   50.658799     Германия   

       city_ru_x  longitude_y  latitude_y country_ru_y    city_ru_y  
0         Берлин    13.404954   52.520007     Германия       Берлин  
1         Мюнхен    11.581981   48.135125     Германия       Мюнхен  
2        Гамбург     9.987170   53.548828     Германия      Гамбург  
3       Нюрнберг    11.074564   49.454288     Германия     Нюрнберг  
4        Лейпциг    12.373075   51.339695     Германия      Лейпциг  
..           ...          ...         ...          ...          ...  
864     Зутермер     4.494025   52.060669   Нидерланды     Зутермер  
865     Цинновиц    13.908474   54.075441     Германия     Цинновиц  
866       Цетель     7.973801   53.418060     Германия       Цетель  
867       Цербст    12.084621   51.966948     Германия       Цербст  
868  Целла-Мелис    10.664964   50.658799     Германия  Целла-Мелис  

[869 rows x 10 columns]

In [ ]:
bar_color = px.colors.qualitative.Pastel[0]

fig = go.Figure(data=[
    go.Bar(
        name='Number of Deals',
        x=deals_by_city_sorted['City'].head(10),
        y=deals_by_city_sorted['Number of Deals'].head(10),
        marker_color=bar_color )])

fig.update_layout(
    title=dict(text="Top 10 Cities by Number of Deals", x=0.5),
    yaxis_title="Number of Deals",
    xaxis_tickangle=0)

fig.show()

In [ ]:
deals_by_city_sorted.to_csv("deals_by_city_sorted.csv", index=False)

In [ ]:
deals_by_city_sorted

City  Number of Deals  longitude_x  latitude_x country_ru_x  \
0          Berlin              264    13.404954   52.520007     Германия   
1         München               88    11.581981   48.135125     Германия   
2         Hamburg               78     9.987170   53.548828     Германия   
3        Nürnberg               53    11.074564   49.454288     Германия   
4         Leipzig               52    12.373075   51.339695     Германия   
..            ...              ...          ...         ...          ...   
864    Zoetermeer                1     4.494025   52.060669   Нидерланды   
865     Zinnowitz                1    13.908474   54.075441     Германия   
866         Zetel                1     7.973801   53.418060     Германия   
867        Zerbst                1    12.084621   51.966948     Германия   
868  Zella-Mehlis                1    10.664964   50.658799     Германия   

       city_ru_x  longitude_y  latitude_y country_ru_y    city_ru_y  
0         Берлин    13.404954   52.520007     Германия       Берлин  
1         Мюнхен    11.581981   48.135125     Германия       Мюнхен  
2        Гамбург     9.987170   53.548828     Германия      Гамбург  
3       Нюрнберг    11.074564   49.454288     Германия     Нюрнберг  
4        Лейпциг    12.373075   51.339695     Германия      Лейпциг  
..           ...          ...         ...          ...          ...  
864     Зутермер     4.494025   52.060669   Нидерланды     Зутермер  
865     Цинновиц    13.908474   54.075441     Германия     Цинновиц  
866       Цетель     7.973801   53.418060     Германия       Цетель  
867       Цербст    12.084621   51.966948     Германия       Цербст  
868  Целла-Мелис    10.664964   50.658799     Германия  Целла-Мелис  

[869 rows x 10 columns]

In [ ]:
deals_geo = deals[deals['City'] != 'Unnamed'].dropna(subset="city_ru")

geometry = [Point(xy) for xy in zip(deals_geo["longitude"], deals_geo["latitude"])]

gdf = gpd.GeoDataFrame(deals_geo, geometry=geometry)

gdf.set_crs(epsg=4326, inplace=True)

display(gdf.head())

Unnamed: 0                   Id  Deal Owner Name Closing Date  Quality  \
32          35  5805028000056714532    Ulysses Adams          NaT      NaN   
39          42  5805028000056731279    Ulysses Adams          NaT      NaN   
49          56  5805028000056683030    Charlie Davis          NaT  C - Low   
50          57  5805028000056568397  Paula Underwood          NaT      NaN   
53          60  5805028000056558351    Ulysses Adams          NaT  C - Low   

                    Stage Lost Reason       Page               Campaign  \
32  Registered on Webinar         NaN   /webinar            webinar1906   
39  Registered on Webinar         NaN   /webinar                    NaN   
49    Waiting For Payment         NaN  /eng/test  performancemax_eng_DE   
50  Registered on Webinar         NaN   /webinar                    NaN   
53    Waiting For Payment         NaN       /eng                    NaN   

            Content  ... Offer Total Amount         Contact Name        City  \
32              NaN  ...                  0  5805028000044019127      Berlin   
39              NaN  ...                  0  5805028000054755989   Lahnstein   
49  _{region_name}_  ...               9000  5805028000056690015  Crailsheim   
50              NaN  ...                  0  5805028000020664131    Prenzlau   
53              NaN  ...               9000  5805028000056578244    Dortmund   

   Level of Deutsch SLA Seconds  longitude   latitude  country_ru  \
32       Неизвестно         NaN  13.404954  52.520007    Германия   
39       Неизвестно         NaN   7.609363  50.307827    Германия   
49       Неизвестно      1239.0  10.063357  49.133735    Германия   
50               B1         NaN  13.862376  53.316844    Германия   
53               B1       589.0   7.465298  51.513587    Германия   

        city_ru                   geometry  
32       Берлин  POINT (13.40495 52.52001)  
39     Ланштайн   POINT (7.60936 50.30783)  
49  Крайльсхайм  POINT (10.06336 49.13374)  
50     Пренцлау  POINT (13.86238 53.31684)  
53     Дортмунд    POINT (7.4653 51.51359)  

[5 rows x 29 columns]

In [ ]:
gdf.geometry.is_empty.sum()

np.int64(0)

In [ ]:
center = gdf.geometry.union_all().centroid
m = folium.Map(location=[center.y, center.x], zoom_start=4)

marker_cluster = MarkerCluster().add_to(m)

for _, row in gdf.iterrows():
    folium.Marker(
        location=[row.geometry.y, row.geometry.x],
        popup=f"Index: {_}"
    ).add_to(marker_cluster)

m.save("deals_map_cluster.html")
m

# Анализ географических данных: основные выводы и рекомендации

Распределение сделок по регионам:

Основная масса сделок в Центральной Европе, лидирует Германия (кластер на карте). Берлин - явный лидер, Мюнхен и Гамбург значительно отстают. Меньшие объемы в Восточной Европе, Ближнем Востоке и Северной Америке (изолированные точки). Наименьшая активность в Северной Америке и части Азии.

Лучшие города по объему сделок:

Берлин (доминирует).
Мюнхен и Гамбург (значительно меньше).
Другие крупные города (Нюрнберг, Лейпциг и др.) - низкие объемы, что подчеркивает концентрацию в нескольких центрах.
Общие выводы:

Германия - ключевой рынок (Берлин, Мюнхен, Гамбург). Умеренная активность в Восточной Европе и на Ближнем Востоке. Минимальное присутствие в США и других мировых рынках.

Рекомендации по расширению рынка:

Рассмотреть расширение в соседние страны Европы и на Ближний Восток.
Изучить барьеры для выхода на рынок США.
Усилить присутствие в других городах Германии, помимо Берлина.

-----------------------------------------------------------------------------------------------------------


# Изучите влияние уровня владения немецким языком на успешность сделок в разных городах.


------------------------------------------------------------------------------------------------------------

Группировка успешных сделок по городу и владению немецким языком

In [ ]:
filtered_deals = deals.dropna(subset=['City', 'Level of Deutsch'])
deals_by_city_lang = (
    filtered_deals.groupby(['City', 'Level of Deutsch'])
    .agg(Total_Deals=('Id', 'count'),
         Successful_Deals=('Stage', lambda x: (x == 'Payment Done').sum()))
    .reset_index()
)

deals_by_city_lang['Success_Rate'] = (
    deals_by_city_lang['Successful_Deals'] / deals_by_city_lang['Total_Deals']
) * 100

print(deals_by_city_lang.head())
print(deals_by_city_lang["Success_Rate"].describe())

        City Level of Deutsch  Total_Deals  Successful_Deals  Success_Rate
0     Aachen               A2            1                 0           0.0
1     Aachen               B1            5                 2          40.0
2     Aachen       Неизвестно            4                 1          25.0
3      Aalen       Неизвестно            3                 0           0.0
4  Abensberg       Неизвестно            1                 0           0.0
count    1188.000000
mean       28.290076
std        39.875795
min         0.000000
25%         0.000000
50%         0.000000
75%        50.000000
max       100.000000
Name: Success_Rate, dtype: float64


In [ ]:
fig_analog = px.bar(
    deals_top_cities,
    x="City",
    y="Total_Deals",
    color="Level of Deutsch",
    title="Общее количество сделок по городам и уровню владения немецким языком (10 лучших городов)",
    labels={"Total_Deals": "Total Deals", "City": "City",
            "Level of Deutsch": ""},
    barmode="group",
    text_auto=True
)

fig_analog.update_layout(
    title_x=0.5,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="center",
        x=0.5,
        title_text=""
    ))
fig_analog.show()

In [ ]:
deals_top_cities.to_csv("deals_top_cities.csv", index=False)

*Заключение*

Носители C1 и B2 демонстрируют высокую успешность, в Дуйсбурге и Кёльне C1 достигает 100%. Успешность варьируется по городам: в Мюнхене, Лейпциге и Кёльне высокие показатели для A2, B1 и B2. Дуйсбург и Гамбург лидируют по успешности на отдельных уровнях. В Берлине и Лейпциге успех распределен равномерно. Города с преобладанием высокого уровня немецкого (B2, C1) показывают лучшие результаты, что подчеркивает важность владения языком.